In [1]:
import tensorflow as tf
import pandas as pd

from stable_baselines.common.policies import MlpLnLstmPolicy
from stable_baselines import PPO2

from tensortrade.strategies import StableBaselinesTradingStrategy
from tensortrade.environments import TradingEnvironment
from tensortrade.rewards import RiskAdjustedReturns
from tensortrade.actions import PairCriteriaSizeActions
from tensortrade.instruments import Quantity, TradingPair, BTC, USD
from tensortrade.wallets import Wallet, Portfolio
from tensortrade.exchanges.simulated import SimulatedExchange
from tensortrade.features.stationarity import FractionalDifference
from tensortrade.features.scalers import MinMaxNormalizer
from tensortrade.features import FeaturePipeline

WINDOW_SIZE = 20
PRICE_COLUMN = 'close'

normalize = MinMaxNormalizer(inplace=True)
difference = FractionalDifference(difference_order=0.6, inplace=True)
feature_pipeline = FeaturePipeline(steps=[normalize, difference])

action_scheme = PairCriteriaSizeActions(USD/BTC)
reward_scheme = RiskAdjustedReturns(return_algorithm="sharpe")

csv_file = tf.keras.utils.get_file(
    'Coinbase_BTCUSD_1h.csv', 'https://www.cryptodatadownload.com/cdd/Coinbase_BTCUSD_1h.csv')
ohlcv_data = pd.read_csv(csv_file, skiprows=1, index_col="Date")
ohlcv_data.columns = map(str.lower, ohlcv_data.columns)
ohlcv_data = ohlcv_data.rename(columns={'volume btc': 'volume'})

# ohlcv_data = pd.read_csv('./data/updateOHLCdata_master.csv')
ohlcv_data = ohlcv_data.iloc[0:10000]

exchange = SimulatedExchange(data_frame=ohlcv_data, price_column=PRICE_COLUMN)

wallets = [(exchange, USD, 10000), (exchange, BTC, 0)]

portfolio = Portfolio(base_instrument=USD, wallet_tuples=wallets)

print('Transformed Data:')
print(exchange.observation_columns)

model = PPO2
policy = MlpLnLstmPolicy
params = {'learning_rate': 1e-5,
          'nminibatches': 1,
          'verbose': 2}

environment = TradingEnvironment(exchange=exchange,
                                 portfolio=portfolio,
                                 action_scheme=action_scheme,
                                 reward_scheme=reward_scheme,
                                 feature_pipeline=feature_pipeline,
                                 window_size=WINDOW_SIZE)

strategy = StableBaselinesTradingStrategy(environment=environment,
                                          model=model,
                                          policy=policy,
                                          model_kwargs=params)

performance = strategy.run(steps=10000)

W1208 16:47:43.835475 4462005696 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/module.py:31: The name tf.enable_resource_variables is deprecated. Please use tf.compat.v1.enable_resource_variables instead.

W1208 16:47:43.855360 4462005696 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:46: The name tf.train.AdadeltaOptimizer is deprecated. Please use tf.compat.v1.train.AdadeltaOptimizer instead.

W1208 16:47:43.856165 4462005696 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:47: The name tf.train.AdagradOptimizer is deprecated. Please use tf.compat.v1.train.AdagradOptimizer instead.

W1208 16:47:43.856890 4462005696 deprecation_wrapper.py:119] From /usr/local/lib/python3.7/site-packages/tensorforce/core/optimizers/tf_optimizer.py:48: The name tf.train.AdamOptimizer is deprecated. Please use tf.compat.v1.train

[None, (<TradeSide.BUY: 'buy'>, USD/BTC, None, 1.0), (<TradeSide.SELL: 'sell'>, USD/BTC, None, 1.0), (<TradeSide.BUY: 'buy'>, USD/BTC, None, 0.5), (<TradeSide.SELL: 'sell'>, USD/BTC, None, 0.5), (<TradeSide.BUY: 'buy'>, USD/BTC, None, 0.3333333333333333), (<TradeSide.SELL: 'sell'>, USD/BTC, None, 0.3333333333333333), (<TradeSide.BUY: 'buy'>, USD/BTC, None, 0.25), (<TradeSide.SELL: 'sell'>, USD/BTC, None, 0.25), (<TradeSide.BUY: 'buy'>, USD/BTC, None, 0.2), (<TradeSide.SELL: 'sell'>, USD/BTC, None, 0.2), (<TradeSide.BUY: 'buy'>, USD/BTC, None, 0.16666666666666666), (<TradeSide.SELL: 'sell'>, USD/BTC, None, 0.16666666666666666), (<TradeSide.BUY: 'buy'>, USD/BTC, None, 0.14285714285714285), (<TradeSide.SELL: 'sell'>, USD/BTC, None, 0.14285714285714285), (<TradeSide.BUY: 'buy'>, USD/BTC, None, 0.125), (<TradeSide.SELL: 'sell'>, USD/BTC, None, 0.125), (<TradeSide.BUY: 'buy'>, USD/BTC, None, 0.1111111111111111), (<TradeSide.SELL: 'sell'>, USD/BTC, None, 0.1111111111111111), (<TradeSide.BUY: 

Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         0.0  8006.02         0.0  9966.733357    2
step  0.171047         0.0  8006.02         0.0  9967.157553    3
step  0.171045         0.0  8006.04         0.0  9939.340175    4
Order:  OrderStatus.CANCELLED | TradeSide.BUY | TradeType.MARKET | USD/BTC | 686.82 USD | None | None
Before base wallet: Balance: 4580.49 USD | Locked: 916.10 USD
Before quote wallet: Balance: 0.38401672 BTC | Locked: 0.00000000 BTC
After base wallet: Balance: 4580.49 USD | Locked: 2.74 USD
After quote wallet: Balance: 0.38401672 BTC | Locked: 0.07718513 BTC
Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047      

step  0.171045         0.0  8006.04         0.0  9939.340175    4
Order:  OrderStatus.CANCELLED | TradeSide.SELL | TradeType.MARKET | USD/BTC | 0.11225875 BTC | None | None
Before base wallet: Balance: 1815.95 USD | Locked: 226.99 USD
Before quote wallet: Balance: 0.67354306 BTC | Locked: 0.00000000 BTC
After base wallet: Balance: 1815.95 USD | Locked: 0.68 USD
After quote wallet: Balance: 0.67354306 BTC | Locked: 0.01919476 BTC
Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         0.0  8006.02         0.0  9966.733357    2
step  0.171047         0.0  8006.02         0.0  9967.157553    3
step  0.171045         0.0  8006.04         0.0  9939.340175    4
Order:  OrderStatus.CANCELLED | TradeSide.BUY | TradeType.MARKET | USD/BTC | 226.99 USD | None | None
Before base wallet: Balance: 1362.47 USD | Locked: 454.16

step  0.171045         0.0  8006.04         0.0  9939.340175    4
Order:  OrderStatus.CANCELLED | TradeSide.SELL | TradeType.MARKET | USD/BTC | 0.07968784 BTC | None | None
Before base wallet: Balance: 586.85 USD | Locked: 0.00 USD
Before quote wallet: Balance: 0.39843581 BTC | Locked: 0.39843582 BTC
After base wallet: Balance: 586.85 USD | Locked: 0.40 USD
After quote wallet: Balance: 0.39843581 BTC | Locked: 0.39840150 BTC
Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         0.0  8006.02         0.0  9966.733357    2
step  0.171047         0.0  8006.02         0.0  9967.157553    3
step  0.171045         0.0  8006.04         0.0  9939.340175    4
Order:  OrderStatus.CANCELLED | TradeSide.SELL | TradeType.MARKET | USD/BTC | 0.39843582 BTC | None | None
Before base wallet: Balance: 391.50 USD | Locked: 195.75

...

Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         0.0  8006.02         0.0  9966.733357    2
step  0.171047         0.0  8006.02         0.0  9967.157553    3
step  0.171045         0.0  8006.04         0.0  9939.340175    4
Order:  OrderStatus.CANCELLED | TradeSide.BUY | TradeType.MARKET | USD/BTC | 0.31 USD | None | None
Before base wallet: Balance: 0.31 USD | Locked: 0.00 USD
Before quote wallet: Balance: 0.75291294 BTC | Locked: 0.09411412 BTC
After base wallet: Balance: 0.31 USD | Locked: 0.09 USD
After quote wallet: Balance: 0.75291294 BTC | Locked: 0.09410067 BTC
Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         0.0  80

Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         0.0  8006.02         0.0  9966.733357    2
step  0.171047         0.0  8006.02         0.0  9967.157553    3
step  0.171045         0.0  8006.04         0.0  9939.340175    4
Order:  OrderStatus.CANCELLED | TradeSide.SELL | TradeType.MARKET | USD/BTC | 0.12099300 BTC | None | None
Before base wallet: Balance: 0.93 USD | Locked: 0.00 USD
Before quote wallet: Balance: 0.00000000 BTC | Locked: 0.84693302 BTC
After base wallet: Balance: 0.93 USD | Locked: 0.00 USD
After quote wallet: Balance: 0.00000000 BTC | Locked: 0.84693302 BTC
Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         

Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         0.0  8006.02         0.0  9966.733357    2
step  0.171047         0.0  8006.02         0.0  9967.157553    3
step  0.171045         0.0  8006.04         0.0  9939.340175    4
Order:  OrderStatus.CANCELLED | TradeSide.BUY | TradeType.MARKET | USD/BTC | 0.29 USD | None | None
Before base wallet: Balance: 0.44 USD | Locked: 0.14 USD
Before quote wallet: Balance: 0.84698699 BTC | Locked: 0.00000000 BTC
After base wallet: Balance: 0.44 USD | Locked: 0.00 USD
After quote wallet: Balance: 0.84698699 BTC | Locked: 0.00002163 BTC
Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         0.0  80

Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         0.0  8006.02         0.0  9966.733357    2
step  0.171047         0.0  8006.02         0.0  9967.157553    3
step  0.171045         0.0  8006.04         0.0  9939.340175    4
Order:  OrderStatus.CANCELLED | TradeSide.SELL | TradeType.MARKET | USD/BTC | 0.09411437 BTC | None | None
Before base wallet: Balance: 0.38 USD | Locked: 0.00 USD
Before quote wallet: Balance: 0.70584613 BTC | Locked: 0.14116923 BTC
After base wallet: Balance: 0.38 USD | Locked: 0.14 USD
After quote wallet: Balance: 0.70584613 BTC | Locked: 0.14114766 BTC
Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         

Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         0.0  8006.02         0.0  9966.733357    2
step  0.171047         0.0  8006.02         0.0  9967.157553    3
step  0.171045         0.0  8006.04         0.0  9939.340175    4
Order:  OrderStatus.CANCELLED | TradeSide.BUY | TradeType.MARKET | USD/BTC | 0.05 USD | None | None
Before base wallet: Balance: 0.38 USD | Locked: 0.06 USD
Before quote wallet: Balance: 0.84700473 BTC | Locked: 0.00000000 BTC
After base wallet: Balance: 0.38 USD | Locked: 0.00 USD
After quote wallet: Balance: 0.84700473 BTC | Locked: 0.00000918 BTC
Portfolio:             BTC  BTC_locked      USD  USD_locked    net_worth step
step  0.171050         0.0  8005.98         0.0  9994.033019    0
step  0.171049         0.0  8006.00         0.0  9976.177018    1
step  0.171047         0.0  80